In [1]:
# 필요한 모듈과 라이브러리를 로딩
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.common.by import By
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.keys import Keys
import pandas as pd
import time, os, math, random, sys, datetime
from datetime import date, timedelta, datetime
import pyautogui
from tqdm import tqdm
import re

# chromedriver 자동 설치
import chromedriver_autoinstaller

from selenium.webdriver.common.action_chains import ActionChains


In [2]:
# 작업 시간과 고유 dir 등 생성
n = time.localtime()
s = '%04d-%02d-%02d' % (n.tm_year, n.tm_mon, n.tm_mday)
s_time = time.time( )


a = datetime.now()-timedelta(days=1)
a = a.strftime('%Y-%m-%d')
b = datetime.now()-timedelta(days=13)
b = b.strftime('%Y-%m-%d')
print(a, b)

2021-05-05 2021-04-23


In [3]:
print("=" *80)
print("         오늘의유머 크롤러입니다.")
print("=" *80)

f_dir = os.path.expanduser('~') + f'\\Desktop\\crawler-bot\\COMMUNITY\\{b}-{a}\\' # 운영체제 상관없이 바탕화면 'crawler-bot' 폴더에 작업

print("=" *80)
print("데이터 크롤링을 시작합니다.")
print("=" *80)

         오늘의유머 크롤러입니다.
데이터 크롤링을 시작합니다.


In [4]:
# 저장될 파일 경로와 이름을 지정
# 파일을 저장할 폴더 위치를 만들고, 중복일 경우 해당 폴더를 삭제하고 새로 생성합니다.
try : 
    os.makedirs(f_dir)
except : pass
else : 
    os.chdir(f_dir)

fc_name=f_dir+'\\'+f'ou.csv'

In [5]:
# 크롤링 데이터가 들어갈 리스트 생성
domain2 = []    # 크롤링 도메인
keyword2 = []   # 크롤링 키워드
title2 = []     # 게시물 제목
user2 = []      # 게시물 작성자
url2 = []       # 게시물 url
time2 = []      # 게시물 작성 시간
view_cnt2 = []  # 게시물 뷰 카운트
like_cnt2 = []  # 추천/공감 카운트
text2 = []      # 게시물 내용
com_cnt2 = []   # 댓글 수
com_user2 = []  # 댓글 user
com_text2 = []  # 댓글 user_id & text

In [6]:
# chromedriver-autoinstaller 이용
chromedriver_autoinstaller.install(cwd=True)

# HEADLESS MODE
options = webdriver.ChromeOptions()
options.add_argument('headless')
options.add_argument('window-size=1920x1080') 
options.add_argument("--disable-gpu")
options.add_experimental_option('excludeSwitches', ['enable-logging'])
options.add_argument("user-agent=Mozilla/5.0 (Macintosh; Intel Mac OS X 10_12_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/61.0.3163.100 Safari/537.36")
args = ["hide_console", ]

# 알림창 끄기
options.add_experimental_option("prefs", {"profile.default_content_setting_values.notifications": 1})

# 웹사이트 접속 후 해당 메뉴로 이동
driver = webdriver.Chrome(options=options,service_args=args)
driver.maximize_window()

In [7]:
# 1. 오늘의유머 크롤링
query_url= ('http://www.todayhumor.co.kr/')

driver.get(query_url)
driver.implicitly_wait(5)

In [8]:
domain1 = "오늘의유머"
print("==========",domain1,"크롤링 진행 중 ==========")

========== 오늘의유머 크롤링 진행 중 ==========


In [9]:
html = driver.page_source
soup = BeautifulSoup(html, 'html.parser')
item_box = soup.find_all(name='tr',attrs={'class':re.compile('view')})
item_box

[<tr class="view list_tr_freeboard" mn="166812">
 <td class="no"><a href="/board/view.php?table=freeboard&amp;no=1960166&amp;s_no=15148632&amp;no_tag=1&amp;kind=total&amp;page=1" style="color:#444;font-size:10px;font-family:Tahoma" target="_top">15148632</a></td>
 <td class="icon"><div class="board_icon_mini freeboard" style='background-image: url("http://www.todayhumor.co.kr/board/images/icon_sprites.png?09");'></div></td>
 <td class="subject"><a href="/board/view.php?table=freeboard&amp;no=1960166&amp;s_no=15148632&amp;kind=total&amp;page=1" target="_top">저 언제 태근해요?</a> <span style="margin-left:4px;"> <img src="http://www.todayhumor.co.kr/board/images/list_icon_mobile.gif" style="vertical-align:middle; margin-bottom:1px;margin-right:5px"/></span> </td>
 <td class="name"><a class="list_name_member" href="list.php?kind=member&amp;mn=166812" target="_blank">TY</a></td>
 <td class="date">21/05/06 19:34</td>
 <td class="hits">1</td>
 <td class="oknok">0</td>
 </tr>,
 <tr class="view list_

In [10]:
page_num = 15   # 현재 페이지 넘버
while_code = 0

while True :
    
    if while_code == 1:
        break

    target_page = f"http://www.todayhumor.co.kr/board/list.php?kind=total&table=total&page={page_num}"
    driver.get(target_page)
    time.sleep(1)

    html = driver.page_source
    soup = BeautifulSoup(html, 'html.parser')
    item_box = soup.find_all(name='tr',attrs={'class':re.compile('view')})

    for i in item_box :
        if len(i) > 1 :
            to_day = a + " 23:59"
            target_day = b
            
            to_day = to_day[2:]
            target_day = target_day[2:]
            
            # 게시글에 날짜가 지정되어 있으면 가져오고 에러로 가져오지 못하면 전 게시물 날짜 사용
            try :
                i.find(name='td', attrs={'class':'date'}).text.strip().replace("/","-")
                post_day = i.find(name='td', attrs={'class':'date'}).text.strip().replace("/","-")
            except :
                pass
            
            if  post_day > to_day :
                print(post_day, to_day)
                pass           
            
            elif post_day >= target_day :
                try :
                    print('href :',i.find(name='td', attrs={'class':'subject'}).find('a')['href'] )


                    target_url = "http://www.todayhumor.co.kr"+i.find(name='td', attrs={'class':'subject'}).find('a')['href']
                    print("target_url :", target_url)
                    driver.get(target_url)
                    time.sleep(1)
                    print("domain :", domain1)
    #                 print("keyword :", keyword)

                    post_html = driver.page_source
                    post_soup = BeautifulSoup(post_html, 'html.parser')
                    post_box = post_soup.find(name='div', attrs={'class':'containerInner'})

                    # title
                    title1 = post_box.find(name='div', attrs={'class':'viewSubjectDiv'}).text.strip().split("\n")[0]     
                    print("title :", title1)

                    # user_id
                    user1 = post_box.find(name='div', attrs={'class':'writerInfoContents'}).find(name='a').text        
                    print("user_id :", user1)
                    
#                     print(f"scout 004 : {post_box.find(name='div', attrs={'class':'writerInfoContents'}).find_all('div')}")
                    
#                     cnt = 0
#                     for info in post_box.find(name='div', attrs={'class':'writerInfoContents'}).find_all('div') :
#                         print(cnt, info)
                        
                    # time
                    time1 = post_box.find(name='div', attrs={'class':'writerInfoContents'}).find_all('div')[6].text.replace("등록시간 : ","").replace("/","-").strip()
                    print("작성 시간 :", time1)

                    # view
                    view_cnt1 = post_box.find(name='div', attrs={'class':'writerInfoContents'}).find_all('div')[3].text.replace("조회수 : ", "")
                    print("조회수 :", view_cnt1)

                    # like
                    try :
                        like_cnt1 = post_box.find(name='div', attrs={'class':'writerInfoContents'}).find_all('div')[2].span.text.replace("추천 : ", "")
                    except :
                        like_cnt1 = 0
                    print("공감/좋아요 수 :", like_cnt1)

                    # text
                    text1 = post_box.find(name='div', attrs={'class':'viewContent'}).text.strip().replace("\n","")
                    print('게시물 내용 :', text1) 

                    # com_cnt
                    try :                    
                        com_cnt1 = post_box.find(name='div', attrs={'class':'writerInfoContents'}).find_all('div')[5].replace("조회수 : ", "").replace("개", "").strip()
                        com_cnt1 = int(com_cnt1)
                    except :
                        com_cnt1 = 0
                                                                                                                                         
                    print("댓글 수 :", com_cnt1)

                    # com_text
                    com_box = post_box.find(name='div', attrs={'id':'memoContainerDiv'})
                    com_list = []
                    user_list = []

                    for j in com_box :

                        if len(j) > 1 :  

                            try :
                                # comment_user_id
                                com_user = j.find(name='span', attrs={'class':'memoName'}).text

                                com_text = j.find(name='div', attrs={'class':'memoContent'}).text.strip().replace("\n","")
                                com_list.append("작성자 :" + com_user + " :: " + com_text)
                                user_list.append(com_user)
                            except :
                                com_list.append("삭제된 댓글입니다.")

                    print("게시물 작성자 :", user_list)
                    print('게시물 댓글 :', com_list)
                    
                    domain2.append(domain1)
    #                 keyword2.append(keyword)
                    title2.append(title1)
                    user2.append(user1)
                    url2.append(target_url)
                    time2.append(time1)
                    view_cnt2.append(view_cnt1)
                    like_cnt2.append(like_cnt1)
                    text2.append(text1)
                    com_cnt2.append(com_cnt1)
                    com_user2.append(user_list)
                    com_text2.append(com_list)

                    print("\n")
                    
                except :
                    print('삭제된 게시물입니다.')
                    domain2.append(domain1)
    #                 keyword2.append(keyword)
                    title2.append('삭제된 게시물입니다.')
                    user2.append('삭제된 게시물입니다.')
                    url2.append('삭제된 게시물입니다.')
                    time2.append('삭제된 게시물입니다.')
                    view_cnt2.append(0)
                    like_cnt2.append(0)
                    text2.append('삭제된 게시물입니다.')
                    com_cnt2.append(0)
                    com_user2.append('삭제된 게시물입니다.')
                    com_text2.append('삭제된 게시물입니다.')


            else :
                print("크롤링을 완료했습니다.")
                while_code = 1
                break
        
    page_num += 1


href : /board/view.php?table=freeboard&no=1960053&s_no=15148182&kind=total&page=15
target_url : http://www.todayhumor.co.kr/board/view.php?table=freeboard&no=1960053&s_no=15148182&kind=total&page=15
domain : 오늘의유머
title : 오늘부터 마당에서 키우기로
user_id : 솔라시도
작성 시간 : 2021-05-05 12:29:30
조회수 : 289
공감/좋아요 수 : 6
게시물 내용 : 지금은 그냥 개집에 넣어놓음  나오자마자 낑낑대길래  생각해보니  얘네 태어나서 처음으로 햇볕쬐는듯
댓글 수 : 0
게시물 작성자 : ['쿸쿠보틀', 'iT개발자', '두줄입니다', 'XIII트레인', '만원잃은천사']
게시물 댓글 : ['작성자 :쿸쿠보틀 :: 큭...\xa0혹독한\xa0한국의\xa0추위를\xa0맛보아랏\xa0새로운\xa0털뭉치들아...!', '작성자 :iT개발자 :: 귀여움을\xa0못\xa0버티시고,\xa0밖으로\xa0보내셨군요.', '작성자 :두줄입니다 :: 두\xa0당\xa010장\xa0총\xa050장인데 다섯마리가\xa0한장에\xa0나오도록\xa0해서\xa010장으로\xa0합의\xa0보시져', '작성자 :XIII트레인 :: 으아아어아으엉', '작성자 :만원잃은천사 :: 추천\xa0안\xa0누르려고\xa0애써봤지만 어쩔\xa0수\xa0없이\xa0나도\xa0모르게\xa0추천.']


href : /board/view.php?table=humordata&no=1903552&s_no=15148181&kind=total&page=15
target_url : http://www.todayhumor.co.kr/board/view.php?table=humordata&no=1903552&s_no=15148181&kind=total&page=15
domain : 오늘의유머
title : 연애의참견) 애인이

domain : 오늘의유머
title : 베이킹 도구들은 전부 구매했는데 어디서 배워야할지...
user_id : 요다야
작성 시간 : 2021-05-05 11:59:15
조회수 : 228
공감/좋아요 수 : 1
게시물 내용 : 제가 매번 국비 학원다니기에는 인턴생활에다 취업준비를하고있어서 좀 그렇고...  취준하면서 베이킹 효율적으로 배울수있는공간이 어디일까요????? 베이킹 너무 하고싶어요 ㅠㅠ
댓글 수 : 0
게시물 작성자 : []
게시물 댓글 : []


href : /board/view.php?table=humordata&no=1903548&s_no=15148173&kind=total&page=15
target_url : http://www.todayhumor.co.kr/board/view.php?table=humordata&no=1903548&s_no=15148173&kind=total&page=15
domain : 오늘의유머
title : 코로나 지원금으로 2억 7천만원 상당 오징어 조형물 만든 지자체
user_id : 감동브레이커
작성 시간 : 2021-05-05 11:53:16
조회수 : 3154
공감/좋아요 수 : 13
게시물 내용 : 아  물론 일본이야기입니다
댓글 수 : 0
게시물 작성자 : ['냐옹냐옹멍멍']
게시물 댓글 : ['작성자 :냐옹냐옹멍멍 :: 아...\xa0다행이다\xa0ㅠㅠㅠㅠ', '삭제된 댓글입니다.']


href : /board/view.php?table=hstone&no=49637&s_no=15148172&kind=total&page=15
target_url : http://www.todayhumor.co.kr/board/view.php?table=hstone&no=49637&s_no=15148172&kind=total&page=15
domain : 오늘의유머
title : 가시멧돼지 덱 ㅋㅋㅋ
user_id : Mach
작성 시간 : 2021-05-05 11:51:36
조회수 : 127
공감/좋아요 수 : 1
게시

domain : 오늘의유머
title : 소개받은 집
user_id : song
작성 시간 : 2021-05-05 11:10:22
조회수 : 265
공감/좋아요 수 : 8
게시물 내용 : 중학교에 다닐 때 집이 불에 타버렸다.   그 집은 나무로 만들어진 오래된 집으로, 비가 새기까지 하는 낡은 곳이었다.   하지만 나를 포함해 가족 모두가 이 집을 마음에 들어해서, 애착을 가지고 살고 있었다.   만약 집에 인격이 있다면 그녀(집)도 우리를 좋아했을 거라고 생각한다.   당시의 나는 그것을 지극히 자연스럽게 생각하고 있었다.       불이 난 원인은 이웃집의 누전이었다.   집은 여러 가구가 다닥다닥 붙어 있는 주택가였다.   겨울철, 건조한데다 나무로 지어졌던 우리 집은 순식간에 타들어갔고, 우리는 몇시간만에 집을 잃었다.   그리고 다음 날부터 새로운 집을 찾기 위해 돌아다니는 나날이 시작되었다.       어느 날 나는 꿈을 꾸었다.   불타버린 집에 혼자서 남아있는 꿈이다.   꿈 속에서 집은 옛날과 다름 없는 모습이었다.   나는 부엌에 서서, [불이 났던 건 꿈이었나봐. 다행이다.] 라며 안도하고 있었다.   그렇지만 자세히 보니 방의 배치가 미묘하게 달랐다.       부엌 벽이 없어지고 본 적이 없는 다른 집에 이어져 있었다.   당황해서 천장을 올려다보고 이음매를 찾아봤지만 지극히 자연스러운 모습으로 두 집은 연결되어 있었다.   [이 두 집은 같은 집이야!]   꿈 속에서 나는 그렇게 외쳤다.       잠에서 깨어나 아침밥을 먹는데 어머니가 [새로 살 집의 후보가 정했어.] 라고 형제들과 나에게 말해주셨다.   지금 임시로 살고 있는 곳에서 가까우니까 각자 가본 다음 의견을 들려달라고 하셨다.   부모님은 아무래도 결정하는 것을 어려워하고 있는 것 같았다.       그 날은 주말이어서 학교가 쉬었기 때문에 나는 바로 그 집을 보러 갔다.   그리고 바로 나는 알아차렸다.   본 기억이 있었다.   이 집은 그 날 밤 꿈에서 봤던 그 집

domain : 오늘의유머
title : 원숭이꿈
user_id : song
작성 시간 : 2021-05-05 10:58:42
조회수 : 153
공감/좋아요 수 : 4
게시물 내용 : 저는 꿈을 꾸고 있었습니다. 전 예전부터 꿈을 꿀 때 ‘아 지금 내가 꿈을 꾸고 있구나’하고 자각을 할 때가 가끔 있었습니다. 이 때도 그랬습니다. 저는 아무도 없는 무인 역에 혼자 있었습니다. ‘꽤나 음침한 꿈이구나.’ 하고 서있는데 갑자기 생기 없는 남자의 목소리로 안내방송이 흘렀습니다.     전철이 들어오고 있습니다. 이 전철에 타게 되면 당신은 무서운 일을 겪게 됩니다.     기이한 안내방송이었습니다. 잠시 뒤 전철이 도착했습니다. 그것은 전철이라기보다는 유원지에서 볼 수 있는 원숭이열차 같은 것이었는데, 얼굴색이 안 좋은 여러 명의 남녀가 일렬로 앉아있었습니다.     전 ‘정말 별난 꿈이구나’하면서도 내 꿈이 내 자신에게 어느 정도 공포심을 줄 수 있을지 시험해보고 싶어져서 타보기로 했습니다. 정말로 무서워서 못 견디겠으면 눈을 뜨면 되니까 하는 생각이었습니다. 전 스스로 꿈을 꾸고 있다는 자각을 하고 있는 때에 한해서 자유롭게 꿈에서 깨어나는 것이 가능했습니다.     전 뒤에서 세 번째 자리에 앉았습니다. 주변에 뜨뜻한 바람이 느껴졌고 이게 정말 꿈인가 싶을 정도의 생생한 현장감이 있었습니다.     출발하겠습니다     안내방송이 흘렀고 전철이 출발했습니다. 과연 어떤 일이 벌어질 것인지, 저는 불안과 기대감에 가슴이 두근거렸습니다. 전철은 역에서 빠져나가더니 바로 터널로 들어갔습니다. 보라색 불빛이 터널 안을 기괴하게 비추고 있었습니다. 전 생각했습니다.     ‘이거, 어렸을 때 유원지에서 탔던 ‘스릴러 카’에서 본 풍경하고 똑 같네. 이것도 원숭이열차인 걸 보면, 어차피 내 기억 속에 있는 장면이 보이는 것일 뿐이잖아. 이게 뭐가 무서워.’     그때 또 다시 안내방송이 들렸습니다.     다음은 회 뜨기……회 뜨기입니다.     회? 생선?......

domain : 오늘의유머
title : 꿈해몽 가능하신분..?
user_id : 오리지널찡찡
작성 시간 : 2021-05-05 10:43:44
조회수 : 83
공감/좋아요 수 : 0
게시물 내용 : 꿈에서 제가 옥탑에 살고 있는데.바로 옆집사람이 죽었다고 가족들이 울고 있고 바닥엔 피 마른 흔적이 있더라구요  저는 친구들이랑 일 갈려고 하다가 그래도 저승 잘 가라고 꽃도 놓고 절도 하고 기도도 해주고 내려오는데 옥탑으로 올라가는 계단에 죽은 아이의 혼이 있는거예요 제가.그냥 올라가면 되는데.왜 안가냐고 바로 올라가서 가족들 보라고 했는데 잘 보더니 노잣돈을 안가져와서 그런데 내일아침에 자기랑 같이 가줄수 있냐 하더라구요  순간 그 말이 너무 무서운데 티내면 안될거 같아서  태연한척 사연은 안타까운데 나는 여기까지 밖에 못하겠다 미안하다 하고 말하는순간 잠에서 깼어요.  진짜 너무 무섭고 섬뜩해서요;  거절했으니 괜찮겠죠^^;???
댓글 수 : 0
게시물 작성자 : []
게시물 댓글 : []


href : /board/view.php?table=panic&no=102270&s_no=15148153&kind=total&page=15
target_url : http://www.todayhumor.co.kr/board/view.php?table=panic&no=102270&s_no=15148153&kind=total&page=15
domain : 오늘의유머
title : 꿈
user_id : song
작성 시간 : 2021-05-05 10:40:34
조회수 : 137
공감/좋아요 수 : 3
게시물 내용 : 재작년 3월 말 체험한 이야기입니다.       어렸을 때부터 나는 막 잠이 들 때쯤 비슷한 꿈을 자주 꾸었습니다.   먼저 흰색과 회색의 파도 무늬가 보입니다.   그리고나서 목소리가 들려옵니다.       [아!]   [어떻게 된거야?]   [꿰뚫고 나갔어.]   [조금 당겨 봐... 무리야?]   [어쩔 수 없네...]       이렇게 말하는 소리가 들리

...

domain : 오늘의유머
title : 과속 주의
user_id : dodon
작성 시간 : 2021-04-23 09:11:58
조회수 : 2208
공감/좋아요 수 : 10
게시물 내용 : 
댓글 수 : 0
게시물 작성자 : ['풀뜯는소', '大星哲也']
게시물 댓글 : ['작성자 :풀뜯는소 :: 부산\xa0버스\xa0막차\xa0맨뒷자석에\xa0타면\xa0저\xa0기능\xa0있음요', '삭제된 댓글입니다.', '작성자 :大星哲也 :: 버스기사입니다.\xa0시내버스는\xa0승객이\xa0많이\xa0없을때\xa0쇼바가\xa0딱딱해서\xa0작은걸\xa0밣아도\xa0외부에서\xa0봤을때는\xa0별차이가\xa0없어도\xa0실내는\xa0와창창합니다.\xa0경험이\xa0없을땐\xa02열좌석에서\xa0보뽀하려던\xa0남녀의\xa0승객이\xa0헤딩으로\xa0아파하는\xa0해피모드도\xa0보았지만\xa0이제는\xa0피할\xa0수\xa0없는\xa0경우\xa0최대한\xa0속도를\xa0줄이고,\xa0다차선의\xa0경우\xa0그\xa0구간을\xa0피해갑니다.\xa0가끔\xa04차로도로에\xa0전\xa0그\xa0구간을\xa0피해\xa03차로로\xa0달리는데\xa0그구간을\xa0모르는\xa0버스기사가\xa04차로\xa0비었다고\xa0신나게\xa0달리다보면\xa0승용차입장에서보명\xa0그런갑다\xa0갑다하지만\xa0제가볼땐\xa0아찔한\xa0경우가\xa0많습니다.\xa0저\xa0만화가\xa0오바가\xa0있지만\xa0굉장히\xa0적절해보입니다.\xa0그렇기때문에\xa0버스운전자분께서는\xa0항상\xa0감속운행,\xa0승객께서는\xa0손잡이를\xa0꼭\xa0잡아주셨음합니다.']


href : /board/view.php?table=freeboard&no=1959299&s_no=15144298&kind=total&page=136
target_url : http://www.todayhumor.co.kr/board/view.php?table=freeboard&no=1959299&s_no=15144

domain : 오늘의유머
title : 아...나보다 더 않씻는 사람도 있네...
user_id : ♡골골백년♡
작성 시간 : 2021-04-23 08:41:49
조회수 : 239
공감/좋아요 수 : 1
게시물 내용 : 집에 뜨신물 안나오나....
댓글 수 : 0
게시물 작성자 : ['수현냐옹~*', '뿌야옹', '☆용사☆']
게시물 댓글 : ['작성자 :수현냐옹~* :: 아재도\xa0좀\xa0씨서요~\xa0ㅋㅋㅋㅋㅋㅋ', '작성자 :뿌야옹 :: 여름빼고 머리는\xa0이틀에\xa0한번ㅋ', '작성자 :☆용사☆ :: 매일\xa0저녁\xa0또는\xa0아침마다\xa0씻는데...']


href : /board/view.php?table=humordata&no=1902146&s_no=15144286&kind=total&page=136
target_url : http://www.todayhumor.co.kr/board/view.php?table=humordata&no=1902146&s_no=15144286&kind=total&page=136
domain : 오늘의유머
title : 기사식당 후기 레전드
user_id : 눈물한스푼
작성 시간 : 2021-04-23 08:33:33
조회수 : 3324
공감/좋아요 수 : 14
게시물 내용 : 
댓글 수 : 0
게시물 작성자 : ['핸슨', '쿸쿠보틀', '몽랑유객', 'CaffeLatte', '예준이아빠']
게시물 댓글 : ['작성자 :핸슨 :: 산지\xa0직송의\xa0모범\xa0사례', '작성자 :쿸쿠보틀 :: 와\xa0그나저나\xa0진짜\xa0맛있겠다...\xa0저녁으로\xa0저거\xa0세명이\xa0먹어도\xa0남겠는데요????', '삭제된 댓글입니다.', '작성자 :몽랑유객 :: 하긴\xa0그럴법도\xa0한게 가까운\xa0위치의\xa0기사와\xa0매치시켜주는거잖슴?ㅎㅎ', '작성자 :CaffeLatte :: 꼬막3개로\xa0유추해보는\xa03인분~!!', '작성자 :예준이아빠 :: 아는\xa0형\xa0배민배달알바로

domain : 오늘의유머
title : 하 정부 인간들 빠져가지고 누가 페이를 묶어서 이렇게 주나...
user_id : 쿸쿠보틀
작성 시간 : 2021-04-23 07:50:05
조회수 : 212
공감/좋아요 수 : 0
게시물 내용 : 너어무 감사합니다 희희      하지만 페이금액에 비해... 건수가 너무 많지 않나요... 적당히 평소처럼 한 80건으로 묶어주면 안되나요..   200개가 넘는 건 에바 아닌가요...
댓글 수 : 0
게시물 작성자 : []
게시물 댓글 : []


href : /board/view.php?table=gomin&no=1788316&s_no=15144278&kind=total&page=136
target_url : http://www.todayhumor.co.kr/board/view.php?table=gomin&no=1788316&s_no=15144278&kind=total&page=136
domain : 오늘의유머
title : 저도 이제 사랑하고 싶어요..♥
user_id : 모바일
작성 시간 : 2021-04-23 07:28:29
조회수 : 689
공감/좋아요 수 : 1
게시물 내용 : 안녕하세요. 작년 이맘때에 답답한 심정으로 글을 썼는데 똑같은 주제로 또 쓰게 되네요ㅎ 그땐 실연의 아픔을 극복하고자 여러 노력을 했는데도 마음이 계속 헛헛하고 우울하다고 썼어요. 댓글이 많이 달리진 않았지만 누군가에게 마음을 털어놓고, 위로를 받아서 감사했습니다.   그렇게 글을 쓴 후에는 소개팅으로 새로운 사람 접하는 재미(썸이랄만한 사람은 없었지만요^^;)도 느끼고 지인이었던 사람과 짧은 연애도 했어요. 그 짧은 연애로 제가 전에 만났던 사람한테 한 잘못을 이번에는 반대로 제가 겪는 것 같았고요..  그 사람과 헤어지고 한동안 잊고 살았던 실연의 아픔이 또 왔어요(전전남친이요ㅜ) 전전남친은 좋은 사람이어서 그런지 새로운 사람과 잘 만나고 있더라고요.  너무 속상했어요. 이 전전사람에 대한 애정은 그때의 추억으로 남겼고 나도 이제 누군

domain : 오늘의유머
title : 로체샤르님 짤왔습니다
user_id : ㄲㅃ
작성 시간 : 2021-04-23 05:56:02
조회수 : 272
공감/좋아요 수 : 6
게시물 내용 : https://imgbox.com/mBlcZzQm     한 7개월만인 거 같아요 헿헤헷.. 이게 그리다가 텀이 좀 생겼더니(중간에 치★수술하고 한동안 컴퓨터에 안 앉음) 무슨 식으로 그리던 건지 기억이 안 나서 엎거나 손 좀 볼까 해서 건들려 하면 손 댈 데가 안 보여서 그냥 마저 그렸습니다.... 출근 전에 끝나서 다행이에요   원본 파일의 33%임다 원본 필요하시면 말씀하십쇼 33%는 4MB인데 100%는 20.2MB거든요 ㅎ..ㅎㅎ 그릴 때 다음 타자 실키님 것도 같이 그려서 반은 되어 있으므로 조만간 그것도 들고 올개오
댓글 수 : 0
게시물 작성자 : ['로체샤르']
게시물 댓글 : ['작성자 :로체샤르 :: 아니\xa0완전\xa0까먹고\xa0있었는데ㅋㅋㅋㅋㅋㅋㅋ세상에...\xa0감사합니다... 원본은\xa0어떻게\xa0받으면\xa0될까요?']


href : /board/view.php?table=star&no=489872&s_no=15144270&kind=total&page=137
target_url : http://www.todayhumor.co.kr/board/view.php?table=star&no=489872&s_no=15144270&kind=total&page=137
domain : 오늘의유머
title : 미나야
user_id : 양파즙눈물
작성 시간 : 2021-04-23 04:21:17
조회수 : 208
공감/좋아요 수 : 8
게시물 내용 : 외부이미지꺄~ㅎㅎ 묘실장님으로 올라가기전 새침한 우리미나ㅋㅋㅋ 근데 미모 진짜 너무 예쁘네 우리미나ㅠㅠ 아름다움 자체인 우리미나리ㅎㅎ                         미나야~ 우리미나 오늘하루도 좋은 하루 보냈나요~ 우리미나 제주도에서 뮤비 촬영도 잘 마치구 왔는데 오늘은 맛난 거 먹으면서 푹

domain : 오늘의유머
title : 세쌍의 쌍둥이 오빠들을 가진 아이
user_id : 포기를모름
작성 시간 : 2021-04-23 01:12:44
조회수 : 2312
공감/좋아요 수 : 11
게시물 내용 : 일루전 어택 가능
댓글 수 : 0
게시물 작성자 : ['바레이타', '存奈齬廉耐']
게시물 댓글 : ['작성자 :바레이타 :: 6명이\xa0다\xa0비슷하네\xa0ㅋㅋ', '작성자 :存奈齬廉耐 :: 형님\xa0~~~\xa0아까\xa0때리셨잖아요\xa0ㅠㅠ', '삭제된 댓글입니다.', '삭제된 댓글입니다.']


href : /board/view.php?table=humordata&no=1902135&s_no=15144257&kind=total&page=137
target_url : http://www.todayhumor.co.kr/board/view.php?table=humordata&no=1902135&s_no=15144257&kind=total&page=137
domain : 오늘의유머
title : 어느 대학생의 가슴아픈 짝사랑
user_id : 포기를모름
작성 시간 : 2021-04-23 00:49:15
조회수 : 2566
공감/좋아요 수 : 13
게시물 내용 : 
댓글 수 : 0
게시물 작성자 : ['포기를모름', '눈물한스푼']
게시물 댓글 : ['작성자 :포기를모름 :: ', '삭제된 댓글입니다.', '작성자 :눈물한스푼 :: ']


href : /board/view.php?table=panic&no=102256&s_no=15144256&kind=total&page=137
target_url : http://www.todayhumor.co.kr/board/view.php?table=panic&no=102256&s_no=15144256&kind=total&page=137
domain : 오늘의유머
title : [단편] 수많은 왕들의 세상
user_id : 묻어가자
작성 시간 : 2021-04-23 00:49:09
조회수 : 596
공감

In [11]:
df = pd.DataFrame()

df['domain'] = pd.Series(domain2)
# df['keyword'] = pd.Series(keyword2)
df['title'] = pd.Series(title2)
df['user_name'] = pd.Series(user2)
df['url'] = pd.Series(url2)
df['date'] = pd.Series(time2)
df['view_cnt'] = pd.Series(view_cnt2)
df['like_cnt'] = pd.Series(like_cnt2)
df['user_text'] = pd.Series(text2)
df['com_cnt'] = pd.Series(com_cnt2)
df['com_text'] = pd.Series(com_text2)

df

domain                                    title writer  \
0     오늘의유머                           오늘부터 마당에서 키우기로   솔라시도   
1     오늘의유머  연애의참견) 애인이 헤어짐을 두려워하지 않는 이유 (feat.이별보험)   냥냥팡팡   
2     오늘의유머                     돈이 되는 건, 뉴스가 빨리 전달된다    딱좋아   
3     오늘의유머                      어린이날 노래에 숨겨진 놀라운 예언  dodon   
4     오늘의유머                      와씨 이사 결심하려니까 엄청 떨리네   ☆용사☆   
...     ...                                      ...    ...   
3682  오늘의유머                             저랑 비슷한 사연 하나  쿵기덕덜렁   
3683  오늘의유머                 포레스트검프 ost - 메인테마 피아노 커버    제이오   
3684  오늘의유머       (문장 연습 오늘의 단어)          손아귀, 성, 탐욕    윤인석   
3685  오늘의유머          6개월간 매일매일 그림 연습 2021.4.22 130일차     늦늦   
3686  오늘의유머                      울째용이 생일 너무 축하해~!!ㅎㅎ  양파즙눈물   

                                                    url                 time  \
0     http://www.todayhumor.co.kr/board/view.php?tab...  2021-05-05 12:29:30   
1     http://www.todayhumor.co.kr/board/view.php?tab...  2021-05-05 12:29:06   
2     http://www.todayhumor.co.kr/board/view.php?tab...  2021-05-05 12:28:02   
3     http://www.todayhumor.co.kr/board/view.php?tab...  2021-05-05 12:24:52   
4     http://www.todayhumor.co.kr/board/view.php?tab...  2021-05-05 12:11:59   
...                                                 ...                  ...   
3682  http://www.todayhumor.co.kr/board/view.php?tab...  2021-04-23 00:28:29   
3683  http://www.todayhumor.co.kr/board/view.php?tab...  2021-04-23 00:18:57   
3684  http://www.todayhumor.co.kr/board/view.php?tab...  2021-04-23 00:15:22   
3685  http://www.todayhumor.co.kr/board/view.php?tab...  2021-04-23 00:03:43   
3686  http://www.todayhumor.co.kr/board/view.php?tab...  2021-04-23 00:00:04   

     view_cnt like_cnt                                            content  \
0         289        6  지금은 그냥 개집에 넣어놓음  나오자마자 낑낑대길래  생각해보니  얘네 태어나서 처...   
1        1701       15  외부이미지  외부이미지  외부이미지  외부이미지   고민남의 여친은 평소에 헤어지자...   
2         279        0  1 기후 변화에도 잘자라는 콩은 소개됐다   2 하루가 다르게 변하는 풍력 발전기에...   
3        2239       12                              그랬다! 너무나 잘 자라고 있었던 것!   
4         225        1                                집주인한테 문자 보내기 직전....   
...       ...      ...                                                ...   
3682     1970       10                                                      
3683      455        3                                          cover 제이오   
3684      141        0  글쓰기 연습 같이 해요!맘에 드는 글이 보이면 대댓글과 추천도 부탁드려요!비평을 원...   
3685      165        1                                              근육근육!   
3686      176        8  외부이미지외부이미지외부이미지외부이미지외부이미지외부이미지외부이미지외부이미지외부이미지외...   

      com_cnt                                           com_text  
0           0  [작성자 :쿸쿠보틀 :: 큭... 혹독한 한국의 추위를 맛보아랏 새로운 털뭉치들아....  
1           0  [삭제된 댓글입니다., 작성자 :Jin.J :: 저정도로 내면이 썩어터진년인데 대체...  
2           0      [작성자 :디독 :: 한국이 뒤쳐져있다고요 ? 니마...탄소 거래제는 아세요 ?]  
3           0                                       [삭제된 댓글입니다.]  
4           0  [작성자 :XIII트레인 :: 전송!!!, 작성자 :만원잃은천사 :: 정해 놓은 날...  
...       ...                                                ...  
3682        0                                                 []  
3683        0  [작성자 :사과나무길 :: , 작성자 :댓글만비공감 :: 왠지 계속 뛰어야 할거 같...  
3684        0                                                 []  
3685        0                                                 []  
3686        0  [작성자 :트와이스 :: 채영 생일 축하해요 ^^ 멤버들과 맛있는거 많이먹고 즐겁고...  

[3687 rows x 10 columns]

In [12]:
# csv 형태로 저장하기
df.to_csv(fc_name,encoding="utf-8-sig",index=False)

e_time = time.time( )
t_time = e_time - s_time

print("\n")
print("=" *80)
print("1.총 소요시간은 %s 초 입니다 " %round(t_time,1))
print("2.파일 저장 완료: csv 파일명 : %s " %fc_name)

driver.quit()
sys.exit("프로그램을 종료합니다.")



1.총 소요시간은 10176.0 초 입니다 
2.파일 저장 완료: csv 파일명 : C:\Users\JPARK-02\Desktop\crawler-bot\COMMUNITY\2021-04-23-2021-05-05\\ou.csv 


SystemExit: 프로그램을 종료합니다.

c:\python39\lib\site-packages\IPython\core\interactiveshell.py:3449: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
